# Read This FIRST

Run prime_factorization.py first, which generates results.csv. Then run this Jupyter notebook.

# Libraries

In [59]:
import numpy as np
import pandas as pd

import plotly.graph_objects as go
import plotly.express as px
cds = ['#19609f', '#0c304f', '#72b1e9'] # discrete color sequence with 3 colors

import locale
locale.setlocale(locale.LC_ALL, '')

from cdf import cdf

import os
if not os.path.exists('figures'):
    os.mkdir('figures')

# Data

In [60]:
df = pd.read_csv('results.csv')
N = len(df)-1
df.head()

Unnamed: 0  prime factor count  smoothness  roughness  \
0           0                   1           1    1000000   
1           1                   1           1    1000000   
2           2                   1           2          2   
3           3                   1           3          3   
4           4                   2           2          2   

   mobius function outcome  square-free; even number of prime factors  \
0                        0                                          0   
1                        1                                          1   
2                       -1                                          0   
3                       -1                                          0   
4                        0                                          0   

   square-free; odd number of prime factors  has a squared prime  is prime  \
0                                         0                    1         1   
1                                         0                    0         1   
2                                         1                    0         1   
3                                         1                    0         1   
4                                         0                    1         0   

   perfect power  powerful number  semiprime  sphenic number  pronic number  
0              0                0          0               0              1  
1              0                1          0               0              0  
2              1                0          0               0              1  
3              1                0          0               0              0  
4              0                1          1               0              0

# Composite Numbers

In [61]:
if (N == 1000000):
    # hard-coded scenario
    data = []
    for n,c in zip([100, 10000, 1000000], cds):
        df_prime_factor_counts = df.iloc[0:n]['prime factor count'].value_counts().sort_index()
        df_prime_factor_counts = np.round(df_prime_factor_counts/df_prime_factor_counts.sum(), 4)
        data.append(go.Bar(name=f'first {n:d} positive integers', x=df_prime_factor_counts.index, y=df_prime_factor_counts.values, marker_color=c))
    layout = go.Layout(
        title=f'Prime Factor Decomposition of the First {100:n}, {10000:n} and {1000000:n} Positive Integers',
        xaxis_title='prime factor count',
        yaxis_title='percentage',
        yaxis=dict(tickformat=".2%"),
        template='plotly_white',
    )
    fig = go.Figure(data=data, layout=layout)
    fig.update_traces(hovertemplate='%{y} of positive integers is decomposed in %{x} prime factors.')
    fig.show()
else:
    # generic
    df_prime_factor_counts = df['prime factor count'].value_counts()
    df_prime_factor_counts = np.round(df_prime_factor_counts/df_prime_factor_counts.sum(), 4)
    fig = px.bar(x=df_prime_factor_counts.index, y=df_prime_factor_counts.values, labels={'x':'prime factor count', 'y':'percentage'}, color_discrete_sequence=cds, title=f'Prime Factor Decomposition of the First {N:n} Positive Integers', template='plotly_white')
    fig.update_layout(
        xaxis_title='prime factor count',
        yaxis_title='percentage',
        yaxis=dict(tickformat=".2%")
    )
    fig.update_traces(hovertemplate='%{y} of positive integers is decomposed in %{x} prime factors.')
    fig.show()
fig.write_html('figures/prime_factor_counts.html')

# Smoothness

In [62]:
cdf_smoothness = cdf(df['smoothness'])
cdf_smoothness
fig = px.scatter(cdf_smoothness, x='rv', y='proba', title=f'Smoothness of the First {N:n} Positive Integers', color_discrete_sequence=cds, template='plotly_white')
fig.update_traces(mode='lines')
fig.update_layout(
    xaxis_title=None,
    yaxis_title='Cumulative Frequency',
    yaxis=dict(tickformat=".2%")
)
fig.update_traces(hovertemplate='%{y} of positive integers is %{x:d}-smooth.')
fig.show()
fig.write_html('figures/smoothness.html')

# Roughness

In [63]:
cdf_roughness = cdf(-df['roughness'])
cdf_roughness['rv'] = -cdf_roughness['rv'] 
fig = px.scatter(cdf_roughness, x='rv', y='proba', title=f'Roughness of the First {N:n} Positive Integers', color_discrete_sequence=cds, template='plotly_white')
fig.update_traces(mode='lines')
fig.update_layout(
    xaxis_title=None,
    yaxis_title='Cumulative Frequency',
    yaxis=dict(tickformat=".2%")
)
fig.update_traces(hovertemplate='%{y} of positive integers is %{x:d}-rough.')
fig.show()
fig.write_html('figures/roughness.html')

# Counts

In [64]:
# Möbius function outcomes
n_squarefree_even = df['square-free; even number of prime factors'].sum()
n_squarefree_odd = df['square-free; odd number of prime factors'].sum()
n_has_squared_prime_factor = df['has a squared prime'].sum() 

# Other counts
n_primes = df['is prime'].sum()
n_powerful_numbers = df['powerful number'].sum()
n_perfect_powers = df['perfect power'].sum()
n_pronic_numbers = df['pronic number'].sum()
n_semiprimes = df['semiprime'].sum()
n_sphenic_numbers =  df['sphenic number'].sum()


## Möbius Function Outcomes

In [65]:
n_total = n_squarefree_even + n_squarefree_odd + n_has_squared_prime_factor
df_mobius = pd.DataFrame({
    'outcome': ['square-free; even number of prime factors', 'square-free; odd number of prime factors', 'has a squared prime'],
    'percentage': np.round([n_squarefree_even/n_total, n_squarefree_odd/n_total, n_has_squared_prime_factor/n_total],2)
})
fig = px.pie(df_mobius, values='percentage', names='outcome', title=f'Mobius function outcome for the First {N:n} Positive Integers', color_discrete_sequence=cds)
fig.update_traces(hovertemplate='%{label}')
fig.show()
fig.write_html('figures/mobius.html')

## Other Counts

In [66]:
df_other_counts = pd.DataFrame({
    'type of number': ['prime', 'semiprimes', 'sphenic numbers', 'perfect powers', 'powerful number', 'pronic numbers'],
    'percentage': np.round([n_primes, n_semiprimes, n_sphenic_numbers, n_perfect_powers, n_powerful_numbers, n_pronic_numbers]/n_total, 4)
})
fig = px.bar(df_other_counts, x='type of number', y='percentage', title=f'Special Number Counts for the First {N:n} Positive Integers', template='plotly_white', color_discrete_sequence=cds)
fig.update_layout(
    xaxis_title=None,
    yaxis_title='Relative Frequency',
    yaxis=dict(tickformat=".2%")
)
fig.update_traces(hovertemplate='%{y} %{x}')
fig.show()
fig.write_html('figures/special_numbers.html')

# Undebated Numbers

In [67]:
s_any_prop = df['is prime'] | df['semiprime'] | df['powerful number'] | df['perfect power'] | df['sphenic number'] | df['pronic number']
s_any_prop[s_any_prop==0].head(20).index

Int64Index([18, 24, 28, 40, 44, 45, 48, 50, 52, 54, 60, 63, 68, 75, 76, 80, 84,
            88, 92, 96],
           dtype='int64')